# Collect github repository information

In addition to data of github repositories which contains package.json which contain one of the interested JS Testing frameworks (See more details in this [kaggle](https://www.kaggle.com/nongnoochr/bq-github-package-deps)), we need addition repository information to perform the analysis and most of information we are interested is not available in the github's public dataset in BigQuery.

Hench, we will use GraphQL and REST apis that GitHub provides to collect those information.

Keep in mind that GitHub has [rate limits](https://developer.github.com/apps/building-github-apps/understanding-rate-limits-for-github-apps/) when requesting data and we need to take this into consideration and this drives our strategy to collect data of over 210k repos

## Data Collection Strategy

1. We will use GraphQL apis to collect repo data of 50 repositories for each request because we can query multiple repo data of multiple repositories that is impossible to do with a single REST call
2. Somehow, we do not get data of some repositories for the GraphQL requests and we will use REST apis to collect missing data for those repos

## Let's start gathering data!

First, import all required packages

In [101]:
import json
import time
import datetime

import pandas as pd
import numpy as np

import requests

### Gather data via GitHub's GraphQL

First, we will create a function which will
* Take a repoistory name and return a list of dictionaries where each of them contains repo information
* We will limit each query to return data of the first 50 repos since it seems to be a pagination limit for this GraphQL query

In [92]:
# See how to get a token here: https://github.blog/2013-05-16-personal-api-tokens/
api_token = "<Your Token>"
headers = {'Authorization': 'token %s' % api_token}

def run_query(query, variables): 
    ''' A simple function to use requests.post to make the API call. Note the json= section. '''
    
    request = requests.post('https://api.github.com/graphql', json={'query': query, 'variables': variables}, headers=headers)
    if request.status_code == 200:
        return request.json()
    else:
        raise Exception("Query failed to run by returning code of {}. {}".format(request.status_code, query))

# Create a GraphQL query that we will use to collect data        
query = '''
query listRepos($queryString: String!) {
  rateLimit {
    cost
    remaining
    resetAt
  }
  search(query: $queryString, type: REPOSITORY, first: 50) {
    repositoryCount
    pageInfo {
      endCursor
      startCursor
    }
    edges {
      node {
        ... on Repository {
          id
          nameWithOwner
          createdAt
          updatedAt
          forkCount
          stargazers {
            totalCount
          }
          releases {
            totalCount
          }
          issues {
            totalCount
          }
          primaryLanguage {
            name
          }
          languages(first:10) {
            nodes {
              name
            }
          }
        }
      }
    }
  }
}
'''

# Test out the query by specifying multiple repo names
variables = {
 "queryString": "repo:facebook/jest repo:mochajs/mocha repo:bevacqua/baal repo:3rd-Eden/node-hashring repo:jerolimov/react-native-layout repo:almende/vis repo:sayden/relay-mongoose-example repo:mhartington/ionic-v2-and-beyond repo:AddJam/ember-image-drop repo:icanjs/file-droplet repo:codeformunich/Muenchen-Transparent repo:oblador/react-native-lightbox repo:RetailMeNotSandbox/jscale repo:michaelgrosner/tribeca"
}


# Get a result of the test query
result = run_query(query, variables) # Execute the query
remaining_rate_limit = result["data"]["rateLimit"]["remaining"] # Drill down the dictionary
print("Remaining rate limit - {}".format(remaining_rate_limit))

Remaining rate limit - 4986


In [93]:
# Inspect the test result
result

{'data': {'rateLimit': {'cost': 1,
   'remaining': 4986,
   'resetAt': '2019-06-29T04:08:01Z'},
  'search': {'repositoryCount': 13,
   'pageInfo': {'endCursor': 'Y3Vyc29yOjEz', 'startCursor': 'Y3Vyc29yOjE='},
   'edges': [{'node': {'id': 'MDEwOlJlcG9zaXRvcnkxNTA2Mjg2OQ==',
      'nameWithOwner': 'facebook/jest',
      'createdAt': '2013-12-10T00:18:04Z',
      'updatedAt': '2019-06-28T20:48:20Z',
      'forkCount': 3542,
      'stargazers': {'totalCount': 26189},
      'releases': {'totalCount': 0},
      'issues': {'totalCount': 4521},
      'primaryLanguage': {'name': 'JavaScript'},
      'languages': {'nodes': [{'name': 'JavaScript'},
        {'name': 'CSS'},
        {'name': 'TypeScript'},
        {'name': 'Shell'}]}}},
    {'node': {'id': 'MDEwOlJlcG9zaXRvcnkxNDUxMzUy',
      'nameWithOwner': 'mochajs/mocha',
      'createdAt': '2011-03-07T18:44:25Z',
      'updatedAt': '2019-06-28T22:29:52Z',
      'forkCount': 2442,
      'stargazers': {'totalCount': 18028},
      'releases': {'

Get a list of interested repo names of data getting from data of github repositories which contains package.json which contain one of the interested JS Testing frameworks that is saved to **'../data/github_package_deps_June_2019.csv'**

In [94]:
df = pd.read_csv('../data/github_package_deps_June_2019.csv')

Create a function which will split a list into n-size chunks and we will use to when querying data using GraphQL

In [95]:
# From https://chrisalbon.com/python/data_wrangling/break_list_into_chunks_of_equal_size/
# Create a function called "chunks" with two arguments, l and n:
def chunks(l, n):
    # For item i in a range that is a length of l,
    for i in range(0, len(l), n):
        # Create an index range for l of n items:
        yield l[i:i+n]

There are **212,922** repositories in github_package_deps_June_2019.csv 

In [96]:
df.shape

(212922, 11)

Then, split a list of all repo names into chunks where each chunk contains only 50 repo names.
With this, we will need to make **4259** requests to GitHub's GraphQL

In [97]:
repo_chunks = list(chunks(df.repo_name.tolist(),50))

In [98]:
len(repo_chunks)

4259

The last chunk contains only 22 repo names

In [99]:
len(repo_chunks[-1])

22

Let's keep writing data to a text file first before creating a final json to prevent from unexpected events (e.g. unexpected error, lost of internet connection, etc.)

Note that we need to put a small pause between each call to respect GitHub's rate limits

In [103]:
raw_data_file = 'temp/raw_data.txt'

In [102]:
with open(raw_data_file, 'w') as myfile:
    
    for cur_idx, cur_chunk in enumerate(repo_chunks):
        
        # Slow down the requests
        time.sleep(1)
        
        print('***** [{}] START chunk#{}" *****'.format(str(datetime.datetime.now()), cur_idx))
        
        query_list = ['repo:' + x for x in cur_chunk]
        query_str = ' '.join(query_list)
        
        variables = {
         "queryString": query_str
        }
        
        result = run_query(query, variables) # Execute the query
        remaining_rate_limit = result["data"]["rateLimit"]["remaining"] # Drill down the dictionary
        print("Remaining rate limit - {}".format(remaining_rate_limit))
    
        queried_data = result['data']['search']['edges']
        for cur_data in queried_data:
            cur_json_str = json.dumps(cur_data['node'])
            myfile.write(cur_json_str + '\n')

***** [2019-06-28 23:09:23.949735] START chunk#0" *****
Remaining rate limit - 4985
***** [2019-06-28 23:09:25.884612] START chunk#1" *****
Remaining rate limit - 4984
***** [2019-06-28 23:09:28.109418] START chunk#2" *****
Remaining rate limit - 4983
***** [2019-06-28 23:09:30.293177] START chunk#3" *****
Remaining rate limit - 4982
***** [2019-06-28 23:09:32.326706] START chunk#4" *****
Remaining rate limit - 4981
***** [2019-06-28 23:09:34.285252] START chunk#5" *****
Remaining rate limit - 4980
***** [2019-06-28 23:09:36.495360] START chunk#6" *****
Remaining rate limit - 4979
***** [2019-06-28 23:09:38.484597] START chunk#7" *****
Remaining rate limit - 4978
***** [2019-06-28 23:09:40.484161] START chunk#8" *****
Remaining rate limit - 4977
***** [2019-06-28 23:09:43.294190] START chunk#9" *****
Remaining rate limit - 4976
***** [2019-06-28 23:09:45.606383] START chunk#10" *****
Remaining rate limit - 4975
***** [2019-06-28 23:09:48.011821] START chunk#11" *****
Remaining rate lim

Remaining rate limit - 4889
***** [2019-06-28 23:13:06.610080] START chunk#97" *****
Remaining rate limit - 4888
***** [2019-06-28 23:13:08.474863] START chunk#98" *****
Remaining rate limit - 4887
***** [2019-06-28 23:13:11.065993] START chunk#99" *****
Remaining rate limit - 4886
***** [2019-06-28 23:13:13.204937] START chunk#100" *****
Remaining rate limit - 4885
***** [2019-06-28 23:13:15.575076] START chunk#101" *****
Remaining rate limit - 4884
***** [2019-06-28 23:13:17.623088] START chunk#102" *****
Remaining rate limit - 4883
***** [2019-06-28 23:13:19.834271] START chunk#103" *****
Remaining rate limit - 4882
***** [2019-06-28 23:13:21.812342] START chunk#104" *****
Remaining rate limit - 4881
***** [2019-06-28 23:13:24.069318] START chunk#105" *****
Remaining rate limit - 4880
***** [2019-06-28 23:13:26.305311] START chunk#106" *****
Remaining rate limit - 4879
***** [2019-06-28 23:13:28.991961] START chunk#107" *****
Remaining rate limit - 4878
***** [2019-06-28 23:13:31.34

***** [2019-06-28 23:16:52.439964] START chunk#192" *****
Remaining rate limit - 4793
***** [2019-06-28 23:16:55.247006] START chunk#193" *****
Remaining rate limit - 4792
***** [2019-06-28 23:16:57.013749] START chunk#194" *****
Remaining rate limit - 4791
***** [2019-06-28 23:16:59.237278] START chunk#195" *****
Remaining rate limit - 4790
***** [2019-06-28 23:17:01.787885] START chunk#196" *****
Remaining rate limit - 4789
***** [2019-06-28 23:17:03.936441] START chunk#197" *****
Remaining rate limit - 4788
***** [2019-06-28 23:17:06.604174] START chunk#198" *****
Remaining rate limit - 4787
***** [2019-06-28 23:17:08.729880] START chunk#199" *****
Remaining rate limit - 4786
***** [2019-06-28 23:17:10.707194] START chunk#200" *****
Remaining rate limit - 4785
***** [2019-06-28 23:17:12.957522] START chunk#201" *****
Remaining rate limit - 4784
***** [2019-06-28 23:17:15.394445] START chunk#202" *****
Remaining rate limit - 4783
***** [2019-06-28 23:17:17.826980] START chunk#203" **

Remaining rate limit - 4698
***** [2019-06-28 23:20:40.221834] START chunk#288" *****
Remaining rate limit - 4697
***** [2019-06-28 23:20:42.452105] START chunk#289" *****
Remaining rate limit - 4696
***** [2019-06-28 23:20:45.091750] START chunk#290" *****
Remaining rate limit - 4695
***** [2019-06-28 23:20:47.041960] START chunk#291" *****
Remaining rate limit - 4694
***** [2019-06-28 23:20:49.028562] START chunk#292" *****
Remaining rate limit - 4693
***** [2019-06-28 23:20:51.473704] START chunk#293" *****
Remaining rate limit - 4692
***** [2019-06-28 23:20:54.647829] START chunk#294" *****
Remaining rate limit - 4691
***** [2019-06-28 23:20:56.831568] START chunk#295" *****
Remaining rate limit - 4690
***** [2019-06-28 23:20:58.983402] START chunk#296" *****
Remaining rate limit - 4689
***** [2019-06-28 23:21:01.192608] START chunk#297" *****
Remaining rate limit - 4688
***** [2019-06-28 23:21:03.753854] START chunk#298" *****
Remaining rate limit - 4687
***** [2019-06-28 23:21:05

***** [2019-06-28 23:24:16.501484] START chunk#383" *****
Remaining rate limit - 4602
***** [2019-06-28 23:24:18.887834] START chunk#384" *****
Remaining rate limit - 4601
***** [2019-06-28 23:24:21.037719] START chunk#385" *****
Remaining rate limit - 4600
***** [2019-06-28 23:24:23.328137] START chunk#386" *****
Remaining rate limit - 4599
***** [2019-06-28 23:24:25.675094] START chunk#387" *****
Remaining rate limit - 4598
***** [2019-06-28 23:24:27.881350] START chunk#388" *****
Remaining rate limit - 4597
***** [2019-06-28 23:24:29.625899] START chunk#389" *****
Remaining rate limit - 4596
***** [2019-06-28 23:24:32.042541] START chunk#390" *****
Remaining rate limit - 4595
***** [2019-06-28 23:24:34.353254] START chunk#391" *****
Remaining rate limit - 4594
***** [2019-06-28 23:24:36.816167] START chunk#392" *****
Remaining rate limit - 4593
***** [2019-06-28 23:24:38.871872] START chunk#393" *****
Remaining rate limit - 4592
***** [2019-06-28 23:24:40.934766] START chunk#394" **

...

***** [2019-06-29 01:35:52.101359] START chunk#3791" *****
Remaining rate limit - 4850
***** [2019-06-29 01:35:54.558644] START chunk#3792" *****
Remaining rate limit - 4849
***** [2019-06-29 01:35:57.025514] START chunk#3793" *****
Remaining rate limit - 4848
***** [2019-06-29 01:35:59.572419] START chunk#3794" *****
Remaining rate limit - 4847
***** [2019-06-29 01:36:01.708071] START chunk#3795" *****
Remaining rate limit - 4846
***** [2019-06-29 01:36:04.096967] START chunk#3796" *****
Remaining rate limit - 4845
***** [2019-06-29 01:36:06.380417] START chunk#3797" *****
Remaining rate limit - 4844
***** [2019-06-29 01:36:08.974012] START chunk#3798" *****
Remaining rate limit - 4843
***** [2019-06-29 01:36:11.370665] START chunk#3799" *****
Remaining rate limit - 4842
***** [2019-06-29 01:36:13.797267] START chunk#3800" *****
Remaining rate limit - 4841
***** [2019-06-29 01:36:16.363622] START chunk#3801" *****
Remaining rate limit - 4840
***** [2019-06-29 01:36:18.304053] START ch

Remaining rate limit - 4756
***** [2019-06-29 01:39:40.412338] START chunk#3886" *****
Remaining rate limit - 4755
***** [2019-06-29 01:39:42.909735] START chunk#3887" *****
Remaining rate limit - 4754
***** [2019-06-29 01:39:45.265123] START chunk#3888" *****
Remaining rate limit - 4753
***** [2019-06-29 01:39:48.212607] START chunk#3889" *****
Remaining rate limit - 4752
***** [2019-06-29 01:39:50.730827] START chunk#3890" *****
Remaining rate limit - 4751
***** [2019-06-29 01:39:52.972650] START chunk#3891" *****
Remaining rate limit - 4750
***** [2019-06-29 01:39:57.056688] START chunk#3892" *****
Remaining rate limit - 4749
***** [2019-06-29 01:39:59.294650] START chunk#3893" *****
Remaining rate limit - 4748
***** [2019-06-29 01:40:01.632968] START chunk#3894" *****
Remaining rate limit - 4747
***** [2019-06-29 01:40:04.227748] START chunk#3895" *****
Remaining rate limit - 4746
***** [2019-06-29 01:40:06.442208] START chunk#3896" *****
Remaining rate limit - 4745
***** [2019-06-

***** [2019-06-29 01:43:23.894402] START chunk#3980" *****
Remaining rate limit - 4661
***** [2019-06-29 01:43:26.650532] START chunk#3981" *****
Remaining rate limit - 4660
***** [2019-06-29 01:43:28.806004] START chunk#3982" *****
Remaining rate limit - 4659
***** [2019-06-29 01:43:31.117250] START chunk#3983" *****
Remaining rate limit - 4658
***** [2019-06-29 01:43:34.027599] START chunk#3984" *****
Remaining rate limit - 4657
***** [2019-06-29 01:43:36.668134] START chunk#3985" *****
Remaining rate limit - 4656
***** [2019-06-29 01:43:38.983482] START chunk#3986" *****
Remaining rate limit - 4655
***** [2019-06-29 01:43:41.572252] START chunk#3987" *****
Remaining rate limit - 4654
***** [2019-06-29 01:43:43.883509] START chunk#3988" *****
Remaining rate limit - 4653
***** [2019-06-29 01:43:46.931405] START chunk#3989" *****
Remaining rate limit - 4652
***** [2019-06-29 01:43:49.179833] START chunk#3990" *****
Remaining rate limit - 4651
***** [2019-06-29 01:43:51.435460] START ch

Remaining rate limit - 4567
***** [2019-06-29 01:47:13.643129] START chunk#4075" *****
Remaining rate limit - 4566
***** [2019-06-29 01:47:16.034577] START chunk#4076" *****
Remaining rate limit - 4565
***** [2019-06-29 01:47:18.591916] START chunk#4077" *****
Remaining rate limit - 4564
***** [2019-06-29 01:47:20.527745] START chunk#4078" *****
Remaining rate limit - 4563
***** [2019-06-29 01:47:22.882993] START chunk#4079" *****
Remaining rate limit - 4562
***** [2019-06-29 01:47:25.449016] START chunk#4080" *****
Remaining rate limit - 4561
***** [2019-06-29 01:47:27.647666] START chunk#4081" *****
Remaining rate limit - 4560
***** [2019-06-29 01:47:30.060758] START chunk#4082" *****
Remaining rate limit - 4559
***** [2019-06-29 01:47:32.074667] START chunk#4083" *****
Remaining rate limit - 4558
***** [2019-06-29 01:47:34.352400] START chunk#4084" *****
Remaining rate limit - 4557
***** [2019-06-29 01:47:37.002008] START chunk#4085" *****
Remaining rate limit - 4556
***** [2019-06-

***** [2019-06-29 01:50:54.028761] START chunk#4169" *****
Remaining rate limit - 4472
***** [2019-06-29 01:50:56.314760] START chunk#4170" *****
Remaining rate limit - 4471
***** [2019-06-29 01:50:59.163424] START chunk#4171" *****
Remaining rate limit - 4470
***** [2019-06-29 01:51:01.406525] START chunk#4172" *****
Remaining rate limit - 4469
***** [2019-06-29 01:51:04.079264] START chunk#4173" *****
Remaining rate limit - 4468
***** [2019-06-29 01:51:07.141775] START chunk#4174" *****
Remaining rate limit - 4467
***** [2019-06-29 01:51:09.709542] START chunk#4175" *****
Remaining rate limit - 4466
***** [2019-06-29 01:51:12.186137] START chunk#4176" *****
Remaining rate limit - 4465
***** [2019-06-29 01:51:15.035071] START chunk#4177" *****
Remaining rate limit - 4464
***** [2019-06-29 01:51:17.494482] START chunk#4178" *****
Remaining rate limit - 4463
***** [2019-06-29 01:51:19.532694] START chunk#4179" *****
Remaining rate limit - 4462
***** [2019-06-29 01:51:22.602966] START ch

We spent around **2 hours** to collect data from GitHub's GraphQL

#### Create a json file

After have a text file containing the repo data collecting from GitHub's GraphQL, we will read it and create a json data out of it

Steps:
1. Read all lines in the .txt file
2. Strip the prepended and appended empty strings of each line
3. Join text of each line with ',' and wrap the combined text with '[]'
4. Save it to a .json file

In [104]:
with open(raw_data_file) as f:
    raw_content = f.readlines()


In [107]:
out_json_name_raw = 'data/github_repos_info_raw.json'

In [106]:
# Remove whitespace characters like `\n` at the end of each line
all_content = [x.strip() for x in raw_content] 

# Assemble json
all_json_str = ','.join(all_content)
out_json_str = '[{}]'.format(all_json_str)


with open(out_json_name_raw, 'w') as f:  
    f.write(out_json_str)


Inspect the newly created json file to ensure that it is properly saved

In [108]:
with open(out_json_name_raw) as json_file:  
    data_repo = json.load(json_file)

In [109]:
data_repo

[{'id': 'MDEwOlJlcG9zaXRvcnk3NjQ1NzYyNQ==',
  'nameWithOwner': '01alchemist/TurboScript',
  'createdAt': '2016-12-14T12:27:18Z',
  'updatedAt': '2019-06-24T11:10:25Z',
  'forkCount': 32,
  'stargazers': {'totalCount': 472},
  'releases': {'totalCount': 2},
  'issues': {'totalCount': 85},
  'primaryLanguage': {'name': 'JavaScript'},
  'languages': {'nodes': [{'name': 'TypeScript'},
    {'name': 'JavaScript'},
    {'name': 'HTML'},
    {'name': 'Shell'},
    {'name': 'Batchfile'},
    {'name': 'CSS'},
    {'name': 'C++'},
    {'name': 'C'},
    {'name': 'WebAssembly'}]}},
 {'id': 'MDEwOlJlcG9zaXRvcnk5NjEyMDM2Mw==',
  'nameWithOwner': '0067ED/vue-block',
  'createdAt': '2017-07-03T14:36:54Z',
  'updatedAt': '2019-06-12T20:07:25Z',
  'forkCount': 4,
  'stargazers': {'totalCount': 38},
  'releases': {'totalCount': 0},
  'issues': {'totalCount': 1},
  'primaryLanguage': {'name': 'JavaScript'},
  'languages': {'nodes': [{'name': 'JavaScript'},
    {'name': 'HTML'},
    {'name': 'Vue'}]}},
 {'

#### Cleaning steps:

The saved json data has nested information that need to be post-processed before we can use. Hence, we will clean this json data and save to a new .json file

* Extract the 'totalCount' data from the ['stargazers', 'releases', 'issues'] keys and set it as value
* Extract out a list of languages and set it to languages
* Keep other data the same

In [126]:
new_data = []
for cur_data in data_repo:
    cur_newdata = {}
    for key, value in cur_data.items():

        if key in ['stargazers', 'releases', 'issues']:
            cur_newdata[key + '_count'] = value['totalCount']
        elif key == 'primaryLanguage':
            # If the primaryLanguage is null, set it to ''
            if value:
                cur_newdata[key] = value['name']
            else:
                cur_newdata[key] = ''
        elif key == 'languages':
            cur_newdata[key] = [x['name'] for x in cur_data['languages']['nodes']]
        else:
            cur_newdata[key] = value
    
    new_data.append(cur_newdata)
    

In [128]:
out_json_name = 'data/github_repos_info.json'

In [129]:
with open(out_json_name, 'w') as fp:
    json.dump(new_data, fp)

Inspect the newly created cleaned json file to ensure that it is properly saved

In [130]:
with open(out_json_name) as json_file:  
    data_repo_new = json.load(json_file)

In [131]:
data_repo_new

[{'id': 'MDEwOlJlcG9zaXRvcnk3NjQ1NzYyNQ==',
  'nameWithOwner': '01alchemist/TurboScript',
  'createdAt': '2016-12-14T12:27:18Z',
  'updatedAt': '2019-06-24T11:10:25Z',
  'forkCount': 32,
  'stargazers_count': 472,
  'releases_count': 2,
  'issues_count': 85,
  'primaryLanguage': 'JavaScript',
  'languages': ['TypeScript',
   'JavaScript',
   'HTML',
   'Shell',
   'Batchfile',
   'CSS',
   'C++',
   'C',
   'WebAssembly']},
 {'id': 'MDEwOlJlcG9zaXRvcnk5NjEyMDM2Mw==',
  'nameWithOwner': '0067ED/vue-block',
  'createdAt': '2017-07-03T14:36:54Z',
  'updatedAt': '2019-06-12T20:07:25Z',
  'forkCount': 4,
  'stargazers_count': 38,
  'releases_count': 0,
  'issues_count': 1,
  'primaryLanguage': 'JavaScript',
  'languages': ['JavaScript', 'HTML', 'Vue']},
 {'id': 'MDEwOlJlcG9zaXRvcnk1Njc1OTEyNQ==',
  'nameWithOwner': '01alchemist/x-ray.js',
  'createdAt': '2016-04-21T09:06:24Z',
  'updatedAt': '2019-04-02T20:58:18Z',
  'forkCount': 6,
  'stargazers_count': 15,
  'releases_count': 0,
  'issues

### Gather data via GitHub's REST apis

Let's inspect a number of repo data we collected from GraphQL

In [133]:
len(data_repo_new)

139077

Now, let's find out how many repos in github_package_deps_June_2019.csv

In [134]:
df_package = pd.read_csv('../data/github_package_deps_June_2019.csv')


In [137]:
df_package.shape

(212922, 11)

In [139]:
df_package.head()

repo_name  \
0                      0-mb/pg-lb   
1    0000-bigtree/binary-protocol   
2  0000000009/selenium-standalone   
3                  001szymon/atom   
4  001szymon/phonegap-app-desktop   

                                         package_dep  mocha   jest  jasmine  \
0                                           pg,mocha   True  False    False   
1    bluebird,expect.js,istanbul,jshint,mocha,should   True  False    False   
2  async,commander,debug,lodash,minimist,mkdirp,r...   True  False    False   
3  async,atom-keymap,babel-core,bootstrap,clear-c...  False  False     True   
4  grunt,grunt-cli,grunt-contrib-copy,grunt-contr...  False  False     True   

   qunit  funcunit  cypress  puppeteer   chai  sinon  
0  False     False    False      False  False  False  
1  False     False    False      False  False  False  
2  False     False    False      False  False  False  
3  False     False    False      False  False  False  
4  False     False    False      False  False  False

Looks like there are a lot of repo that we don't get repo data, let's look into those project

In [136]:
df_repo = pd.DataFrame.from_dict(data_repo_new)

In [138]:
df_repo.shape

(139077, 10)

In [140]:
df_repo.head()

createdAt  forkCount                                id  \
0  2016-12-14T12:27:18Z         32  MDEwOlJlcG9zaXRvcnk3NjQ1NzYyNQ==   
1  2017-07-03T14:36:54Z          4  MDEwOlJlcG9zaXRvcnk5NjEyMDM2Mw==   
2  2016-04-21T09:06:24Z          6  MDEwOlJlcG9zaXRvcnk1Njc1OTEyNQ==   
3  2014-04-22T20:54:02Z          4  MDEwOlJlcG9zaXRvcnkxOTA0NTg0OA==   
4  2016-09-08T12:09:44Z          5  MDEwOlJlcG9zaXRvcnk2NzY5OTg1NQ==   

   issues_count                                          languages  \
0            85  [TypeScript, JavaScript, HTML, Shell, Batchfil...   
1             1                            [JavaScript, HTML, Vue]   
2             0                     [JavaScript, TypeScript, HTML]   
3             5                                 [JavaScript, HTML]   
4             0  [C++, Makefile, Batchfile, Shell, TypeScript, ...   

              nameWithOwner primaryLanguage  releases_count  stargazers_count  \
0   01alchemist/TurboScript      JavaScript               2               472   
1          0067ED/vue-block      JavaScript               0                38   
2      01alchemist/x-ray.js      JavaScript               0                15   
3     007design/gulp-prefix      JavaScript               0                 7   
4  01alchemist/x-ray-kernel             C++               0                 5   

              updatedAt  
0  2019-06-24T11:10:25Z  
1  2019-06-12T20:07:25Z  
2  2019-04-02T20:58:18Z  
3  2017-03-05T09:42:21Z  
4  2018-10-18T07:33:47Z

Get a list of repo names with missing data

In [141]:
missing_repos = list(set(df_package['repo_name']) - set(df_repo['nameWithOwner']))

In [143]:
len(missing_repos)

74587

Let's inspect the first few

In [144]:
missing_repos[:5]

['yugangw-msft/azure-rest-api-specs',
 'corimf/cordova-cli',
 'wikibus/heracles',
 'AleksueiR/gulp',
 'emilybsessions/cgm-remote-monitor']

Somehow, we don't get data for some repos because graphql returns nothing but REST apis return data for a lot of those repos.

Let's get data for the missing repos using REST apis!

Steps:
1. Get a list of column names of the current repo dataset so we can create a new one which contains the same information
2. Specify a list of interested key names in data returned from the REST request
3. Iterate through each repo with missing data and construct an output data
4. Write each data to a text file
5. Create a json file from the final text file

In [148]:
df_repo.columns.tolist()

['createdAt',
 'forkCount',
 'id',
 'issues_count',
 'languages',
 'nameWithOwner',
 'primaryLanguage',
 'releases_count',
 'stargazers_count',
 'updatedAt']

In [ ]:
col_list = [
 'id',
 'nameWithOwner',
 'createdAt',
 'updatedAt'
 'forkCount',
 'stargazers_count',
 'releases_count',
 'issues_count',
 'primaryLanguage',
 'languages'
]

Test drive a REST request to see a structure of the returned data and determine how to initialized data 

In [145]:
url = "https://api.github.com/repos/wikibus/heracles"
res=requests.get(url,headers=headers)
repos=res.json()

In [146]:
repos

{'id': 55887007,
 'node_id': 'MDEwOlJlcG9zaXRvcnk1NTg4NzAwNw==',
 'name': 'Alcaeus',
 'full_name': 'wikibus/Alcaeus',
 'private': False,
 'owner': {'login': 'wikibus',
  'id': 8124371,
  'node_id': 'MDEyOk9yZ2FuaXphdGlvbjgxMjQzNzE=',
  'avatar_url': 'https://avatars1.githubusercontent.com/u/8124371?v=4',
  'gravatar_id': '',
  'url': 'https://api.github.com/users/wikibus',
  'html_url': 'https://github.com/wikibus',
  'followers_url': 'https://api.github.com/users/wikibus/followers',
  'following_url': 'https://api.github.com/users/wikibus/following{/other_user}',
  'gists_url': 'https://api.github.com/users/wikibus/gists{/gist_id}',
  'starred_url': 'https://api.github.com/users/wikibus/starred{/owner}{/repo}',
  'subscriptions_url': 'https://api.github.com/users/wikibus/subscriptions',
  'organizations_url': 'https://api.github.com/users/wikibus/orgs',
  'repos_url': 'https://api.github.com/users/wikibus/repos',
  'events_url': 'https://api.github.com/users/wikibus/events{/privacy}',

Let's keep writing data to a text file first before creating a final json to prevent from unexpected events (e.g. unexpected error, lost of internet connection, etc.)

Note that we need to put a small pause between each call to respect GitHub's rate limits

In [151]:
raw_missing_data_file = 'temp/raw_missing_data.txt'

In [155]:
with open(raw_missing_data_file, 'w') as myfile:
    
    for cur_idx, cur_repo_name in enumerate(missing_repos):
        
        # Slow down the requests
        time.sleep(0.75)
        
        print('***** [{}] START repo#{}: {}" *****'.format(str(datetime.datetime.now()), cur_idx, cur_repo_name))
        
        # Initialize data
        cur_data = {}
        cur_data['id'] = ''
        cur_data['nameWithOwner'] = cur_repo_name
        cur_data['createdAt'] = ''
        cur_data['updatedAt'] = ''
        cur_data['forkCount'] = ''
        cur_data['stargazers_count'] = ''
        cur_data['releases_count'] = -1
        cur_data['issues_count'] = -1
        cur_data['primaryLanguage'] = ''
        cur_data['languages'] = []
        
        # Make a request. Fallback to the default data if any error occurs
        try:
            url = "https://api.github.com/repos/" + cur_repo_name
            res=requests.get(url,headers=headers)
            repos=res.json()
            
            cur_data['id'] = repos['node_id']
            cur_data['createdAt'] = repos['created_at']
            cur_data['updatedAt'] = repos['updated_at']
            cur_data['forkCount'] = repos['forks_count']
            cur_data['stargazers_count'] = repos['stargazers_count']
            cur_data['releases_count'] = -1
            cur_data['issues_count'] = repos['open_issues_count']
            cur_data['primaryLanguage'] = repos['language']
            cur_data['languages'] = []
            
        except:
            print("Cannot retrieve data for this repo")
        
        # Write json string to file
        cur_json_str = json.dumps(cur_data)
        myfile.write(cur_json_str + '\n')


***** [2019-06-29 12:24:02.223853] START repo#0: yugangw-msft/azure-rest-api-specs" *****
***** [2019-06-29 12:24:03.205055] START repo#1: corimf/cordova-cli" *****
***** [2019-06-29 12:24:04.201237] START repo#2: wikibus/heracles" *****
***** [2019-06-29 12:24:05.268286] START repo#3: AleksueiR/gulp" *****
***** [2019-06-29 12:24:06.240564] START repo#4: emilybsessions/cgm-remote-monitor" *****
***** [2019-06-29 12:24:07.284703] START repo#5: techthumb/hospitalrun-frontend" *****
***** [2019-06-29 12:24:08.285909] START repo#6: mbroadst/thinky" *****
***** [2019-06-29 12:24:09.268333] START repo#7: Keystion/platform.js" *****
Cannot retrieve data for this repo
***** [2019-06-29 12:24:10.167658] START repo#8: kaylynyuh/401-mid-quarter-project" *****
Cannot retrieve data for this repo
***** [2019-06-29 12:24:11.094547] START repo#9: rtablada/ember-moment" *****
***** [2019-06-29 12:24:12.081096] START repo#10: strongloop/express" *****
***** [2019-06-29 12:24:13.152545] START repo#11: g

***** [2019-06-29 12:25:39.131216] START repo#95: danieljx/jsonwebtoken.github.io" *****
***** [2019-06-29 12:25:40.136677] START repo#96: twistedogic/vue" *****
Cannot retrieve data for this repo
***** [2019-06-29 12:25:41.048908] START repo#97: Dashed/eslint" *****
***** [2019-06-29 12:25:42.049727] START repo#98: cianclarke/fh-connector-sharepoint-cloud" *****
***** [2019-06-29 12:25:43.047452] START repo#99: egee-irl/egee-bot" *****
***** [2019-06-29 12:25:44.274314] START repo#100: pairyo/redux" *****
***** [2019-06-29 12:25:45.372979] START repo#101: levabd/persony" *****
***** [2019-06-29 12:25:46.398175] START repo#102: erictsangx/angular" *****
***** [2019-06-29 12:25:47.365313] START repo#103: vschoettke/react-select" *****
***** [2019-06-29 12:25:48.332924] START repo#104: qweasd1/ngJsTree" *****
***** [2019-06-29 12:25:49.311649] START repo#105: nomilous/mocha-fork" *****
***** [2019-06-29 12:25:50.364395] START repo#106: icefoggy/flux" *****
***** [2019-06-29 12:25:51.4475

***** [2019-06-29 12:27:15.314335] START repo#191: jden/ninvoke" *****
***** [2019-06-29 12:27:16.340267] START repo#192: lucassus/karma-sinon-chai" *****
***** [2019-06-29 12:27:17.312296] START repo#193: stevemilburn/subnet-info" *****
***** [2019-06-29 12:27:18.341135] START repo#194: kormik/angular" *****
***** [2019-06-29 12:27:19.309481] START repo#195: lqqqqf/bootstrap" *****
***** [2019-06-29 12:27:20.469273] START repo#196: mabrasil/resistance.js" *****
***** [2019-06-29 12:27:21.490746] START repo#197: tranhuucuong91/glossary" *****
***** [2019-06-29 12:27:22.542162] START repo#198: denisov-vlad/redash" *****
***** [2019-06-29 12:27:23.542447] START repo#199: vicb/i18n" *****
***** [2019-06-29 12:27:24.523539] START repo#200: GabrielNicolasAvellaneda/riak-nodejs-client" *****
***** [2019-06-29 12:27:25.489812] START repo#201: frankvdp/django" *****
***** [2019-06-29 12:27:26.452919] START repo#202: santiagogil/metalsmith-simple-shortcodes" *****
***** [2019-06-29 12:27:27.445

***** [2019-06-29 12:28:52.462172] START repo#288: yola/browserify-i18n" *****
***** [2019-06-29 12:28:53.469660] START repo#289: aknuds1/html-to-react" *****
***** [2019-06-29 12:28:54.487383] START repo#290: voyages-sncf-technologies/ngA11y" *****
***** [2019-06-29 12:28:55.461439] START repo#291: ammeep/grunt-electron-installer" *****
***** [2019-06-29 12:28:56.469641] START repo#292: ellisonbg/vega-lite" *****
***** [2019-06-29 12:28:57.447214] START repo#293: AshKyd/pixi.js" *****
***** [2019-06-29 12:28:58.429756] START repo#294: StephanieMak/chosen" *****
***** [2019-06-29 12:28:59.399804] START repo#295: mafintosh/node-sodium-prebuilt" *****
***** [2019-06-29 12:29:00.475101] START repo#296: ifandelse/postal.js" *****
***** [2019-06-29 12:29:01.439980] START repo#297: aldopizzagalli/accessopolis" *****
***** [2019-06-29 12:29:02.702330] START repo#298: ONE-LOGIC/gulp-modular-karma" *****
***** [2019-06-29 12:29:03.740120] START repo#299: snowypowers/neon-js" *****
***** [2019-0

***** [2019-06-29 12:30:30.864423] START repo#385: alchapone/alchapone.github.io" *****
Cannot retrieve data for this repo
***** [2019-06-29 12:30:31.765997] START repo#386: ilyes14/chosen" *****
***** [2019-06-29 12:30:32.801277] START repo#387: TallyFox/ui-router" *****
***** [2019-06-29 12:30:33.814726] START repo#388: phoenixbox/bell" *****
***** [2019-06-29 12:30:34.794644] START repo#389: donkirkby/django" *****
***** [2019-06-29 12:30:35.746970] START repo#390: ssk7833/redux" *****
***** [2019-06-29 12:30:36.728615] START repo#391: turingou/working" *****
***** [2019-06-29 12:30:37.749636] START repo#392: slucero/generator-web-starter" *****
***** [2019-06-29 12:30:38.785755] START repo#393: boyanes90/expofruta" *****
***** [2019-06-29 12:30:39.981003] START repo#394: hubandbob/Snap.svg" *****
***** [2019-06-29 12:30:41.097559] START repo#395: jameree/pixi.js" *****
***** [2019-06-29 12:30:42.091175] START repo#396: Hstry/ember-responds-to" *****
***** [2019-06-29 12:30:43.21547

...

***** [2019-06-30 09:24:35.264865] START repo#74123: kevinfng/bootstrap" *****
***** [2019-06-30 09:24:36.267114] START repo#74124: msxdrew/falcor" *****
***** [2019-06-30 09:24:37.313681] START repo#74125: ryanwilliamquinn/sails-permissions" *****
***** [2019-06-30 09:24:38.410109] START repo#74126: csc111vs/ember-cli-search-text" *****
***** [2019-06-30 09:24:39.459001] START repo#74127: pixelass/schachtel" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:24:40.375490] START repo#74128: Jeremy017/angular-timer" *****
***** [2019-06-30 09:24:41.343552] START repo#74129: matobet/userportal" *****
***** [2019-06-30 09:24:42.373364] START repo#74130: drKraken/array-chunk" *****
***** [2019-06-30 09:24:43.374305] START repo#74131: idolize/react-router" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:24:44.294870] START repo#74132: casaaga/retinajs" *****
***** [2019-06-30 09:24:45.316985] START repo#74133: aeei/ax5ui-kernel" *****
Cannot retrieve data for this r

***** [2019-06-30 09:26:10.528877] START repo#74217: EESimulations/DLCSim" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:26:11.516491] START repo#74218: jay3126/canvas-lms" *****
***** [2019-06-30 09:26:12.641665] START repo#74219: FuZhenn/maptalks.js" *****
***** [2019-06-30 09:26:13.696570] START repo#74220: eddieloeffen/cucumber-js" *****
***** [2019-06-30 09:26:14.780037] START repo#74221: dallonf/babel-loader" *****
***** [2019-06-30 09:26:15.785526] START repo#74222: nimiq-network/jungle-db" *****
***** [2019-06-30 09:26:16.816027] START repo#74223: asux/ember-cli-bootstrap-datetimepicker" *****
***** [2019-06-30 09:26:17.765445] START repo#74224: kishoremallick/ng2-carnival" *****
***** [2019-06-30 09:26:18.800255] START repo#74225: jbt/eslint" *****
***** [2019-06-30 09:26:19.768731] START repo#74226: simsgj/socket.io" *****
***** [2019-06-30 09:26:20.754439] START repo#74227: STRML/babel-loader" *****
***** [2019-06-30 09:26:21.729308] START repo#74228: SG-Yang

***** [2019-06-30 09:27:43.397453] START repo#74309: krahman/hopscotch" *****
***** [2019-06-30 09:27:44.423748] START repo#74310: Percona-QA/pmm-qa" *****
***** [2019-06-30 09:27:45.558594] START repo#74311: lucasmonteverde/instagram-top-picks" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:27:46.520427] START repo#74312: tab58/ndarray-blas-level2" *****
***** [2019-06-30 09:27:47.526372] START repo#74313: dahal/kona" *****
***** [2019-06-30 09:27:48.691602] START repo#74314: nigelspencer/contractor" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:27:49.604004] START repo#74315: travis4all/CoffeeScript-Compiler" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:27:50.518049] START repo#74316: Japroriple/ripple-client" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:27:51.460416] START repo#74317: ochukai/angular.js" *****
***** [2019-06-30 09:27:52.572321] START repo#74318: wavii/jade" *****
***** [2019-06-30 09:27:53.638580] STAR

***** [2019-06-30 09:29:19.978860] START repo#74403: gunchleoc/django" *****
***** [2019-06-30 09:29:20.961583] START repo#74404: sanjarito/wdi-fundamentals-rps" *****
***** [2019-06-30 09:29:21.953921] START repo#74405: BrandwatchLtd/axiom" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:29:22.886322] START repo#74406: mcanthony/famin" *****
***** [2019-06-30 09:29:23.895469] START repo#74407: evantbyrne/polydom" *****
Cannot retrieve data for this repo
***** [2019-06-30 09:29:24.834812] START repo#74408: keyvanfatehi/node-serialport" *****
***** [2019-06-30 09:29:25.930093] START repo#74409: niwamaxou/RpgBlocNote" *****
***** [2019-06-30 09:29:26.955365] START repo#74410: lwahonen/engine.io-client" *****
***** [2019-06-30 09:29:27.969240] START repo#74411: cloudzombie/openassets-js" *****
***** [2019-06-30 09:29:28.923286] START repo#74412: MaxGraey/mapnik-xml-to-mapbox-gl-json" *****
***** [2019-06-30 09:29:29.925573] START repo#74413: kyledrake/coinpunk-bitcoinjs" ***

***** [2019-06-30 09:30:56.727034] START repo#74498: 22222/ArnoldC.js" *****
***** [2019-06-30 09:30:57.709736] START repo#74499: VANITAX/jade" *****
***** [2019-06-30 09:30:58.674568] START repo#74500: kemitchell/npm" *****
***** [2019-06-30 09:30:59.696089] START repo#74501: peakon/mailgun-email-validation" *****
***** [2019-06-30 09:31:00.743269] START repo#74502: quis/govuk_frontend_toolkit" *****
***** [2019-06-30 09:31:01.820656] START repo#74503: vivek8943/sigma.js" *****
***** [2019-06-30 09:31:02.839554] START repo#74504: JacobCWard/fllscoring" *****
***** [2019-06-30 09:31:03.832372] START repo#74505: DelvarWorld/react-draggable" *****
***** [2019-06-30 09:31:04.883491] START repo#74506: defbyte/sir-trevor-js" *****
***** [2019-06-30 09:31:05.926909] START repo#74507: eduOS/write-good" *****
***** [2019-06-30 09:31:06.906108] START repo#74508: appersonlabs/react-native" *****
***** [2019-06-30 09:31:07.972149] START repo#74509: dennisgaebel/svg-gradient-cleaner" *****
***** [

Note that it takes over **20 hours** to collect data of **74586** repositories

Read the text data and save it to a json file

In [157]:
with open(raw_missing_data_file) as f:
    raw_missing_content = f.readlines()

In [159]:
out_json_name_missing = 'data/github_repos_info_raw_missing.json'

In [164]:
# Remove whitespace characters like `\n` at the end of each line
all_content = [x.strip() for x in raw_missing_content] 

# Assemble json
all_json_str = ','.join(all_content)
out_json_str = '[{}]'.format(all_json_str)


with open(out_json_name_missing, 'w') as f:  
    f.write(out_json_str)

Inspect the newly created cleaned json file to ensure that it is properly saved

In [166]:
with open(out_json_name_missing) as json_file:  
    data_repo_missing = json.load(json_file)

In [167]:
data_repo_missing

[{'id': 'MDEwOlJlcG9zaXRvcnk0MTExMjM1OA==',
  'nameWithOwner': 'yugangw-msft/azure-rest-api-specs',
  'createdAt': '2015-08-20T18:29:33Z',
  'updatedAt': '2019-05-06T19:23:46Z',
  'forkCount': 0,
  'stargazers_count': 0,
  'releases_count': -1,
  'issues_count': 0,
  'primaryLanguage': 'TypeScript',
  'languages': []},
 {'id': 'MDEwOlJlcG9zaXRvcnkxMzIyMjA4NQ==',
  'nameWithOwner': 'corimf/cordova-cli',
  'createdAt': '2013-09-30T17:37:26Z',
  'updatedAt': '2014-12-10T14:46:08Z',
  'forkCount': 1,
  'stargazers_count': 0,
  'releases_count': -1,
  'issues_count': 0,
  'primaryLanguage': 'JavaScript',
  'languages': []},
 {'id': 'MDEwOlJlcG9zaXRvcnk1NTg4NzAwNw==',
  'nameWithOwner': 'wikibus/heracles',
  'createdAt': '2016-04-10T07:47:30Z',
  'updatedAt': '2019-06-28T06:48:53Z',
  'forkCount': 3,
  'stargazers_count': 30,
  'releases_count': -1,
  'issues_count': 10,
  'primaryLanguage': 'TypeScript',
  'languages': []},
 {'id': 'MDEwOlJlcG9zaXRvcnk0MDkxOTAzOA==',
  'nameWithOwner': 'Ale

## Combined repo data from GraphQL and REST

After getting data for all interested repo, let's combined them and create a new csv which contains all of those data

In [168]:
len(data_repo_missing)

74587

In [176]:
len(data_repo_new)

139077

In [177]:
data_repo_combine = data_repo_new + data_repo_missing

In [178]:
len(data_repo_combine)

213664

Create a new pandas dataframe from the combined data

In [179]:
df_repo_combined = pd.DataFrame.from_dict(data_repo_combine)

In [189]:
df_repo_combined.head()

createdAt forkCount                           node_id  \
0  2016-12-14T12:27:18Z        32  MDEwOlJlcG9zaXRvcnk3NjQ1NzYyNQ==   
1  2017-07-03T14:36:54Z         4  MDEwOlJlcG9zaXRvcnk5NjEyMDM2Mw==   
2  2016-04-21T09:06:24Z         6  MDEwOlJlcG9zaXRvcnk1Njc1OTEyNQ==   
3  2014-04-22T20:54:02Z         4  MDEwOlJlcG9zaXRvcnkxOTA0NTg0OA==   
4  2016-09-08T12:09:44Z         5  MDEwOlJlcG9zaXRvcnk2NzY5OTg1NQ==   

   issues_count                                          languages  \
0            85  [TypeScript, JavaScript, HTML, Shell, Batchfil...   
1             1                            [JavaScript, HTML, Vue]   
2             0                     [JavaScript, TypeScript, HTML]   
3             5                                 [JavaScript, HTML]   
4             0  [C++, Makefile, Batchfile, Shell, TypeScript, ...   

                  repo_name primaryLanguage  releases_count stargazers_count  \
0   01alchemist/TurboScript      JavaScript               2              472   
1          0067ED/vue-block      JavaScript               0               38   
2      01alchemist/x-ray.js      JavaScript               0               15   
3     007design/gulp-prefix      JavaScript               0                7   
4  01alchemist/x-ray-kernel             C++               0                5   

              updatedAt  
0  2019-06-24T11:10:25Z  
1  2019-06-12T20:07:25Z  
2  2019-04-02T20:58:18Z  
3  2017-03-05T09:42:21Z  
4  2018-10-18T07:33:47Z

Then, rename and re-order columns before saving it to a csv file

In [182]:
df_repo_combined = df_repo_combined.rename(columns={"nameWithOwner": "repo_name", "id": "node_id", "forkCount": "forks_count"})

In [192]:
df_repo_combined.columns.tolist()

['createdAt',
 'forks_count',
 'node_id',
 'issues_count',
 'languages',
 'repo_name',
 'primaryLanguage',
 'releases_count',
 'stargazers_count',
 'updatedAt']

In [193]:
new_cols = [
    'repo_name',
    'createdAt',
    'updatedAt',
    'stargazers_count',
    'releases_count',
    'issues_count',
    'forks_count',
    'primaryLanguage',
    'languages',
    'node_id'
 ]

Inspect the updated dataframe

In [195]:
df_repo_combined = df_repo_combined[new_cols]

In [196]:
df_repo_combined.sample(20)

repo_name  \
78723                      jsreport/jsreport-wkhtmltopdf   
92879                            miaowjs/miaow-amd-parse   
187167           Manbeardo/angular-ui-router-breadcrumbs   
96598                        muminoff/flatui-boilerplate   
125529  the-economist-editorial/component-silver-tab-bar   
134837                                wolfeidau/mqtt-rpc   
4866                                     Chunam/angular2   
32524                          arunghosh/react-pin-input   
191111                      marcoturi/ionic2-boilerplate   
3918                                     BuonOmo/webquiz   
138816                            zqWu/json_format_check   
179517                    DyslexicChris/Folio-Handlebars   
140337                               soulcutter/ember.js   
136944                               ymkjp/hakase-client   
193368                                     rlugojr/async   
144019                      sivakumar-kailasam/ember-cli   
1973                              Annojirao/reactYoutube   
17032                      Oteng/sails-sql-converter-cli   
105622                                  pgilad/gulp-sort   
24768                           YPlan/react-sticky-stack   

                   createdAt             updatedAt stargazers_count  \
78723   2015-05-21T12:45:35Z  2019-02-28T23:27:39Z                6   
92879   2015-06-18T03:45:59Z  2017-03-02T09:26:21Z                1   
187167  2015-01-17T18:45:23Z  2016-01-24T15:19:57Z                0   
96598   2014-02-24T10:19:46Z  2014-02-24T10:26:17Z                0   
125529  2016-02-03T13:36:07Z  2016-05-12T11:52:09Z                0   
134837  2013-09-05T01:45:43Z  2019-05-14T11:48:17Z               21   
4866    2016-07-01T10:50:34Z  2016-07-01T10:51:31Z                0   
32524   2017-03-06T04:18:13Z  2019-06-05T16:48:29Z               21   
191111  2016-09-29T09:44:01Z  2019-06-07T01:45:43Z              310   
3918    2016-09-11T15:55:09Z  2018-11-25T22:33:00Z                1   
138816  2015-02-15T06:06:07Z  2016-06-29T04:36:55Z                0   
179517  2015-02-09T22:12:07Z  2015-03-10T00:11:38Z                1   
140337  2015-01-21T00:08:22Z  2015-01-26T16:26:43Z                0   
136944  2015-02-17T01:46:46Z  2015-04-11T10:45:42Z                0   
193368  2016-01-05T04:52:15Z  2016-01-13T06:37:27Z                0   
144019  2016-07-13T16:31:45Z  2016-07-13T16:31:47Z                0   
1973    2017-07-26T03:39:36Z  2017-07-26T03:56:39Z                0   
17032   2016-12-13T13:07:32Z  2016-12-16T11:03:29Z                1   
105622  2015-01-01T10:35:54Z  2019-02-25T16:40:23Z               21   
24768   2015-12-18T10:33:01Z  2019-04-23T08:21:56Z               27   

        releases_count  issues_count forks_count primaryLanguage  \
78723               22             6           4      JavaScript   
92879                0             0           0      JavaScript   
187167              -1             0           0      JavaScript   
96598                0             0           0             CSS   
125529               0             0           0            HTML   
134837               0             2           7      JavaScript   
4866                 0             0           0      TypeScript   
32524                1             8          14      JavaScript   
191111              -1             4         106      JavaScript   
3918                 5             0           0            HTML   
138816               0             0           0      JavaScript   
179517              -1             0           0      JavaScript   
140337              -1             0           0      JavaScript   
136944               0             0           0      JavaScript   
193368              -1             0           0      JavaScript   
144019              -1             0           0      JavaScript   
1973                 0             0           0      JavaScript   
17032                0             1           1      JavaScript   
10

Every

In [197]:
df_repo_combined.to_csv('data/github_repo_for_package_deps_June_2019.csv', index=False)